In [1]:
# import matplotlib.pyplot as plt
# import numpy as np
# import pystac_client
# import pyproj
# from odc import stac as odc_stac

# eodc_catalog = pystac_client.Client.open(
#     "https://stac.eodc.eu/api/v1",
# )

# aoi = (8.0, 50.0, 8.2, 50.2)  # (minx, miny, maxx, maxy)

# time_range_eu = "2024-03-01/2024-03-15"

# search_eu = eodc_catalog.search(
#     collections=["SENTINEL1_SIG0_20M"], bbox=aoi, datetime=time_range_eu
# )
# items_eu = search_eu.item_collection()
# crs = pyproj.CRS.from_wkt(items_eu[0].properties["proj:wkt2"])
# resolution = items_eu[0].properties["gsd"]

# dc = odc_stac.load(
#     items_eu,
#     bbox=aoi,
#     crs=crs,
#     bands=["VV", "VH"],
#     resolution=resolution,
#     chunks={"x": 1000, "y": 1000, "time": -1},
# )

In [2]:
import os
import hvplot.xarray  # noqa
import numpy as np
import pystac_client
import xarray as xr
from dask.distributed import Client, wait
from odc import stac as odc_stac

In [3]:
client = Client(processes=False, threads_per_worker=2, n_workers=3, memory_limit="12GB")
chunks = {"time": 1, "latitude": 1300, "longitude": 1300}
client

<Client: 'inproc://10.10.18.118/1699727/1' processes=3 threads=6, memory=33.53 GiB>

/eodc/private/tuwgeo/users/mabdelaa/anaconda3/envs/cnn/lib/python3.12/site-packages/rasterio/warp.py:387: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  dest = _reproject(
/eodc/private/tuwgeo/users/mabdelaa/anaconda3/envs/cnn/lib/python3.12/site-packages/rasterio/warp.py:387: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  dest = _reproject(
Aborting load due to failure while reading: s3://esa-worldcover/v200/2021/map/ESA_WorldCover_10m_2021_v200_N54E012_Map.tif:1
Aborting load due to failure while reading: s3://esa-worldcover/v200/2021/map/ESA_WorldCover_10m_2021_v200_N54E012_Map.tif:1
Aborting load due to failure while reading: s3://esa-worldcover/v200/2021/map/ESA_WorldCover_10m_2021_v200_N54E012_Map.tif:1
Aborting load due to failure while reading: s3://esa-worldcover/v200/2021/map/ESA_WorldCover_10m_2021_v200_N54E012_Map.tif:1
Aborting load due to failure whi

In [4]:
# Coordinate Reference System - World Geodetic System 1984 (WGS84) in this case
crs = "EPSG:4326"
res = 0.00018  # 20 meter in degree


time_range = "2023-10-11/2023-10-25"
minlon, maxlon = 12.3, 13.1
minlat, maxlat = 54.3, 54.6
bounding_box = [minlon, minlat, maxlon, maxlat]
eodc_catalog = pystac_client.Client.open("https://stac.eodc.eu/api/v1")


search = eodc_catalog.search(
    collections="SENTINEL1_SIG0_20M",
    bbox=bounding_box,
    datetime=time_range,
)

items_sig0 = search.item_collection()
items_sig0

In [5]:
def extract_orbit_names(items):
    return np.array(
        [
            items[i].properties["sat:orbit_state"][0].upper()
            + str(items[i].properties["sat:relative_orbit"])
            for i in range(len(items))
        ]
    )


def post_process_eodc_cube(dc: xr.Dataset, items, bands):
    if not isinstance(bands, tuple):
        bands = tuple([bands])
    for i in bands:
        dc[i] = post_process_eodc_cube_(
            dc[i], items, i
        )  # https://github.com/TUW-GEO/dask-flood-mapper.git
    return dc


def post_process_eodc_cube_(dc: xr.Dataset, items, band):
    scale = items[0].assets[band].extra_fields.get("raster:bands")[0]["scale"]
    nodata = items[0].assets[band].extra_fields.get("raster:bands")[0]["nodata"]
    return dc.where(dc != nodata) / scale


bands = "VV"
sig0_dc = odc_stac.load(
    items_sig0,
    bands=bands,
    crs=crs,
    chunks=chunks,
    resolution=res,
    bbox=bounding_box,
    resampling="bilinear",
    groupby=None,
)

In [6]:
sig0_dc = (
    post_process_eodc_cube(sig0_dc, items_sig0, bands)
    .rename_vars({"VV": "sig0"})
    .assign_coords(orbit=("time", extract_orbit_names(items_sig0)))
    .dropna(dim="time", how="all")
    .sortby("time")
)

In [7]:
__, indices = np.unique(sig0_dc.time, return_index=True)
indices.sort()
orbit_sig0 = sig0_dc.orbit[indices].data
sig0_dc = sig0_dc.groupby("time").mean(skipna=True)
sig0_dc = sig0_dc.assign_coords(orbit=("time", orbit_sig0))
sig0_dc = sig0_dc.persist()
wait(sig0_dc)
sig0_dc

<xarray.Dataset> Size: 267MB
Dimensions:      (time: 9, latitude: 1668, longitude: 4445)
Coordinates:
  * latitude     (latitude) float64 13kB 54.6 54.6 54.6 54.6 ... 54.3 54.3 54.3
  * longitude    (longitude) float64 36kB 12.3 12.3 12.3 12.3 ... 13.1 13.1 13.1
    spatial_ref  int32 4B 4326
  * time         (time) datetime64[ns] 72B 2023-10-11T05:33:18 ... 2023-10-25...
    orbit        (time) <U4 144B 'D66' 'D95' 'A146' 'A146' ... 'A44' 'D66' 'D95'
Data variables:
    sig0         (time, latitude, longitude) float32 267MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>

In [8]:
search = eodc_catalog.search(collections="SENTINEL1_HPAR", bbox=bounding_box)

items_hpar = search.item_collection()


bands = ("C1", "C2", "C3", "M0", "S1", "S2", "S3", "STD")
hpar_dc = odc_stac.load(
    items_hpar,
    bands=bands,
    crs=crs,
    chunks=chunks,
    resolution=res,
    bbox=bounding_box,
    groupby=None,
)

hpar_dc = post_process_eodc_cube(hpar_dc, items_hpar, bands).rename({"time": "orbit"})
hpar_dc["orbit"] = extract_orbit_names(items_hpar)
hpar_dc = hpar_dc.groupby("orbit").mean(skipna=True)

In [9]:
hpar_dc = hpar_dc.sel(orbit=orbit_sig0)
hpar_dc = hpar_dc.persist()
wait(hpar_dc)
hpar_dc

<xarray.Dataset> Size: 2GB
Dimensions:      (orbit: 9, latitude: 1668, longitude: 4445)
Coordinates:
  * latitude     (latitude) float64 13kB 54.6 54.6 54.6 54.6 ... 54.3 54.3 54.3
  * longitude    (longitude) float64 36kB 12.3 12.3 12.3 12.3 ... 13.1 13.1 13.1
    spatial_ref  int32 4B 4326
  * orbit        (orbit) object 72B 'D66' 'D95' 'A146' ... 'A44' 'D66' 'D95'
Data variables:
    C1           (orbit, latitude, longitude) float32 267MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    C2           (orbit, latitude, longitude) float32 267MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    C3           (orbit, latitude, longitude) float32 267MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    M0           (orbit, latitude, longitude) float32 267MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    S1           (orbit, latitude, longitude) float32 267MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    S2           (orbit, latitude, longitude) float32 267MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    S3           (orbit, latitude, longitude) float32 267MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    STD          (orbit, latitude, longitude) float32 267MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>

In [10]:
search = eodc_catalog.search(collections="SENTINEL1_MPLIA", bbox=bounding_box)

items_plia = search.item_collection()

bands = "MPLIA"
plia_dc = odc_stac.load(
    items_plia,
    bands=bands,
    crs=crs,
    chunks=chunks,
    resolution=res,
    bbox=bounding_box,
    groupby=None,
)

plia_dc = post_process_eodc_cube(plia_dc, items_plia, bands).rename({"time": "orbit"})
plia_dc["orbit"] = extract_orbit_names(items_plia)
plia_dc = plia_dc.groupby("orbit").mean(skipna=True)

plia_dc = plia_dc.sel(orbit=orbit_sig0)
plia_dc = plia_dc.persist()
wait(plia_dc)
plia_dc

<xarray.Dataset> Size: 267MB
Dimensions:      (orbit: 9, latitude: 1668, longitude: 4445)
Coordinates:
  * latitude     (latitude) float64 13kB 54.6 54.6 54.6 54.6 ... 54.3 54.3 54.3
  * longitude    (longitude) float64 36kB 12.3 12.3 12.3 12.3 ... 13.1 13.1 13.1
    spatial_ref  int32 4B 4326
  * orbit        (orbit) object 72B 'D66' 'D95' 'A146' ... 'A44' 'D66' 'D95'
Data variables:
    MPLIA        (orbit, latitude, longitude) float32 267MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>

In [11]:
os.environ["AWS_NO_SIGN_REQUEST"] = "YES"
wcover_catalog = pystac_client.Client.open("https://services.terrascope.be/stac/")


search = wcover_catalog.search(
    collections="urn:eop:VITO:ESA_WorldCover_10m_2021_AWS_V2", bbox=bounding_box
)

items_wcover = search.item_collection()


wcover_dc = (
    odc_stac.load(
        items_wcover,
        crs=crs,
        chunks=chunks,
        resolution=res,
        bbox=bounding_box,
    )
    .squeeze("time")
    .drop_vars("time")
    .rename_vars({"ESA_WORLDCOVER_10M_MAP": "wcover"})
)
wcover_dc = wcover_dc.persist()
wait(wcover_dc)
wcover_dc

<xarray.Dataset> Size: 30MB
Dimensions:      (latitude: 1668, longitude: 4445)
Coordinates:
  * latitude     (latitude) float64 13kB 54.6 54.6 54.6 54.6 ... 54.3 54.3 54.3
  * longitude    (longitude) float64 36kB 12.3 12.3 12.3 12.3 ... 13.1 13.1 13.1
    spatial_ref  int32 4B 4326
Data variables:
    wcover       (latitude, longitude) float32 30MB dask.array<chunksize=(1300, 1300), meta=np.ndarray>

In [12]:
flood_dc = xr.merge([sig0_dc, plia_dc, hpar_dc, wcover_dc])
flood_dc = flood_dc.where(flood_dc.wcover != 80)
flood_dc = (
    flood_dc.reset_index("orbit", drop=True)
    .rename({"orbit": "time"})
    .dropna(dim="time", how="all", subset=["sig0"])
)
flood_dc = flood_dc.persist()
wait(flood_dc)
flood_dc

RasterioIOError: CURL error: Could not resolve host: esa-worldcover.s3.default.amazonaws.com